## Xarray and ERA5

## Overview:

1. Programmatically request a specific date from the [RDA ERA-5 THREDDS repository](https://rda.ucar.edu/thredds/catalog/files/g/ds633.0/catalog.html)
1. Create a time loop and create products of interest for each time in the loop

## Prerequisites

| Concepts | Importance | Notes |
| --- | --- | --- |
| Xarray  | Necessary | |

* **Time to learn**: 30 minutes
***

## Imports

In [ ]:
import xarray as xr
import numpy as np
import pandas as pd
from pandas.tseries.offsets import MonthEnd,MonthBegin
import cartopy.feature as cfeature
import cartopy.crs as ccrs
import requests
from datetime import datetime, timedelta
import warnings
import metpy.calc as mpcalc
from metpy.units import units
import matplotlib.pyplot as plt

## Programmatically request a specific date from the [RDA ERA-5 THREDDS repository](https://rda.ucar.edu/thredds/catalog/files/g/ds633.0/catalog.html)

The next several cells set the date/time, creates the URL strings, and retrieves selected grids from RDA.

### For this notebook, we choose the ["Cleveland Superbomb"](https://en.wikipedia.org/wiki/Great_Blizzard_of_1978) case of January 26, 1978.

In [ ]:
# Select your date and time here
year = 1978
month = 1
day = 26
hour = 0

<div class="alert alert-danger">
    <b>One-day limit:</b> <br>
    While <b>Xarray</b> can create datasets and data arrays from multiple files, via its <code>open_mfdataset</code> method, this method does not reliably work when reading from a THREDDS server such as RDA's. Therefore, please restrict your temporal range to no more than one calendar day in this notebook.
        </div>

In [ ]:
validTime = datetime(year, month, day, hour)
YYYYMM = validTime.strftime("%Y%m")
YYYYMMDD = validTime.strftime("%Y%m%d")

Among the many tools for time series analysis that Pandas provides are functions to determine the first and last days of a month.

In [ ]:
monthEnd = pd.to_datetime(YYYYMM, format='%Y%m') + MonthEnd(0)
mEndStr = monthEnd.strftime('%Y%m%d23')

monthBeg = pd.to_datetime(YYYYMM, format='%Y%m') + MonthBegin(0)
mBegStr = monthBeg.strftime('%Y%m%d00')

dayBegStr = YYYYMMDD + '00'
dayEndStr = YYYYMMDD + '23'

dayBeg = datetime.strptime(dayBegStr, '%Y%m%d%H')
dayEnd = datetime.strptime(dayEndStr, '%Y%m%d%H')

In [ ]:
dayBeg, dayEnd

In [ ]:
monthBeg, monthEnd

Create the URLs for the various grids.

In [ ]:
SfcURL = []
SfcURL.append('https://rda.ucar.edu/thredds/dodsC/files/g/ds633.0/e5.oper.an.')
SfcURL.append(YYYYMM + '/e5.oper.an')
SfcURL.append('.ll025')
SfcURL.append('.' + mBegStr + '_' + mEndStr + '.nc')
print(SfcURL)

PrsURL = []
PrsURL.append('https://rda.ucar.edu/thredds/dodsC/files/g/ds633.0/e5.oper.an.')
PrsURL.append(YYYYMM + '/e5.oper.an')
PrsURL.append('.ll025')
PrsURL.append('.' +  dayBegStr + '_' + dayEndStr + '.nc' )
print(PrsURL)

ds_urlZ = PrsURL[0] + 'pl/' + PrsURL[1] + '.pl.128_129_z' + PrsURL[2] + 'sc' + PrsURL[3]
ds_urlQ = PrsURL[0] + 'pl/' + PrsURL[1] + '.pl.128_133_q' + PrsURL[2] + 'sc' + PrsURL[3]
ds_urlT = PrsURL[0] + 'pl/' + PrsURL[1] + '.pl.128_130_t' + PrsURL[2] + 'sc' + PrsURL[3]
# Notice that U and V use "uv" instead of "sc" in their name!
ds_urlU = PrsURL[0] + 'pl/' + PrsURL[1] + '.pl.128_131_u' + PrsURL[2] + 'uv' + PrsURL[3]
ds_urlV = PrsURL[0] + 'pl/' + PrsURL[1] + '.pl.128_132_v' + PrsURL[2] + 'uv' + PrsURL[3]

ds_urlU10 = SfcURL[0] + 'sfc/' + SfcURL[1] + '.sfc.128_165_10u' + SfcURL[2] + 'sc' + SfcURL[3]
ds_urlV10 = SfcURL[0] + 'sfc/' + SfcURL[1] + '.sfc.128_166_10v' + SfcURL[2] + 'sc' + SfcURL[3]
ds_urlSLP = SfcURL[0] + 'sfc/' + SfcURL[1] + '.sfc.128_151_msl' + SfcURL[2] + 'sc' + SfcURL[3]

<div class="alert alert-info">NOTE: You can find tables listing all of the various parameters in the ERA-5 datasets at <a href="https://rda.ucar.edu/datasets/ds633.0/?hash=access#!docs">this link</a>

Use your RDA credentials to access these individual NetCDF files. You should have previously registered with RDA, and then saved your user id and password in your home directory as .rdarc , with permissions such that only you have read/write access.

In [ ]:
#Retrieve login credential for RDA.
from pathlib import Path
HOME = str(Path.home())
credFile = open(HOME+'/.rdarc','r')
userId, pw = credFile.read().split()

Connect to the RDA THREDDS server and point to the files of interest. Here, we'll comment out the ones we are not interested in but can always uncomment when we want them. 

In [ ]:
session = requests.Session()
session.auth = (userId, pw)
#storeU10 = xr.backends.PydapDataStore.open(ds_urlU10, session=session)
#storeV10 = xr.backends.PydapDataStore.open(ds_urlV10, session=session)
storeSLP = xr.backends.PydapDataStore.open(ds_urlSLP, session=session)
#storeQ = xr.backends.PydapDataStore.open(ds_urlQ, session=session)
#storeT = xr.backends.PydapDataStore.open(ds_urlT, session=session)
#storeU = xr.backends.PydapDataStore.open(ds_urlU, session=session)
#storeV = xr.backends.PydapDataStore.open(ds_urlV, session=session)
storeZ = xr.backends.PydapDataStore.open(ds_urlZ, session=session)

In [ ]:
ds_urlSLP

In [ ]:
#dsU10 = xr.open_dataset(storeU10)
#dsV10 = xr.open_dataset(storeV10)
dsSLP = xr.open_dataset(storeSLP)
#dsQ   = xr.open_dataset(storeQ)
#dsT   = xr.open_dataset(storeT)
#dsU   = xr.open_dataset(storeU)
#dsV   = xr.open_dataset(storeV)
dsZ   = xr.open_dataset(storeZ)

### Examine the datasets

The surface fields span the entire month. Let's restrict the range so it matches the day of interest.

In [ ]:
dsSLP = dsSLP.sel(time=slice(dayBeg,dayEnd))

In [ ]:
dsSLP

Create an Xarray DataArray object for SLP and perform unit conversion

In [ ]:
SLP = dsSLP['MSL']
SLP = SLP.metpy.convert_units('hPa')

Now examine the geopotential data on isobaric surfaces.

In [ ]:
dsZ

To reduce the memory footprint for data on isobaric surfaces, let's request only 6 out of the 37 available levels.

In [ ]:
dsZ = dsZ.sel(level = [200,300,500,700,850,1000])

In [ ]:
Z = dsZ['Z']

In [ ]:
Z

Set contour levels for both SLP and Z. 

In [ ]:
slpLevels = np.arange(900,1080,4)

Choose a particular isobaric surface.

In [ ]:
pLevel = 500

Redefine Z so it consists only of the data at the level you just chose.

In [ ]:
Z = Z.sel(level=pLevel)

For the purposes of plotting geopotential heights in decameters, choose an appropriate contour interval and range of values ... for geopotential heights, a common convention is: from surface up through 700 hPa: 3 dam; above that, 6 dam to 400 and then 9 or 12 dam from 400 and above.

In [ ]:
if (pLevel == 1000):
    zLevels= np.arange(-90,63, 3)
elif (pLevel == 850):
    zLevels = np.arange(60, 183, 3)
elif (pLevel == 700):
    zLevels = np.arange(201, 339, 3)
elif (pLevel == 500):
    zLevels = np.arange(468, 606, 6)
elif (pLevel == 300):
    zLevels = np.arange(765, 1008, 9)
elif (pLevel == 200): 
    zLevels = np.arange(999, 1305, 9)

<div class="alert alert-info">In this notebook, we did not retrieve the U- and V- wind component grids. However, if you end up modifying this notebook to do so, uncomment the lines in the following cell.</div>

In [ ]:
#print (U.units)
## Convert wind from m/s to knots; use MetPy to calculate the wind speed.
#UKts = U.metpy.convert_units('knots')
#VKts = V.metpy.convert_units('knots')
## Calculate windspeed.
#wspdKts = calc.wind_speed(U,V).to('knots')

Create objects for the relevant coordinate arrays; in this case, *longitude*, *latitude*, and *time*.

In [ ]:
lons, lats, times= SLP.longitude, SLP.latitude, SLP.time

Take a peek at a couple of these coordinate arrays.

In [ ]:
lons

In [ ]:
times

Create contour plots of SLP, and overlay Natural Earth coastlines and borders.

<div class="alert alert-info">The overall look of our plot depends on many settings. Part of the fun (and challenge) of making plots is playing around with these settings ... such as contour line/fill intervals; line styles and thicknesses, and so on. There really is no "one size fits all" set of methods and arguments for a meteorological visualization ... every case is different. </div>

Next, we will create maps for each hour of our chosen day. We will create *for* loops to do so, iterating through each hour of the day. We will group all of our map plotting code into a couple of functions; one for a global view, and the other regional. Then we will call each function in our loop. 

First, create a function that will create a global map using the **Plate Carree** projection. This is the projection that is used for visualizations on [NOAA's Science on a Sphere](https://www.google.com/url?sa=t&rct=j&q=&esrc=s&source=web&cd=&cad=rja&uact=8&ved=2ahUKEwiy3KHG-tj6AhVIKFkFHTmLAgQQFnoECAwQAQ&url=https%3A%2F%2Fsos.noaa.gov%2F&usg=AOvVaw0Jk0LClAPTR5aNngu9W3Cz), such as the one we have here in ETEC!

In [ ]:
def make_global_map(i, z):
    
    res = '110m'
    fig = plt.figure(figsize=(18,12))
    ax = plt.subplot(1,1,1,projection=ccrs.PlateCarree())
    ax.set_global()
    ax.add_feature(cfeature.COASTLINE.with_scale(res))
    ax.add_feature(cfeature.STATES.with_scale(res))

    # Add the title
    valTime = pd.to_datetime(SLP.time[i].values).strftime("%m/%d/%Y at %H UTC")
    tl1 = str("ERA-5 SLP and " + str(pLevel) + "hPa Z, " + valTime)
    plt.title(tl1,fontsize=16)

    # Height (Z) contour fills
    
    CF = ax.contourf(lons,lats,z,levels=zLevels,cmap=plt.get_cmap('viridis'), extend='both')
    cbar = fig.colorbar(CF,shrink=0.5)
    cbar.set_label(r'Heights (dam)', size='medium')
    
    # SLP contour lines
    CL = ax.contour(lons,lats,SLP.isel(time=i),slpLevels,linewidths=1.25,colors='chocolate')
    ax.clabel(CL, inline_spacing=0.2, fontsize=8, fmt='%.0f');   

Now, create a regional map, focusing on our weather event of interest. First, set some values relevant to the regional map projection and extent.

In [ ]:
lonW = -110.0
lonE = -70.0
latS = 20.0
latN = 50.0
cLon = (lonW + lonE) / 2.
cLat = (latS + latN) / 2.
proj_map = ccrs.LambertConformal(central_longitude=cLon, central_latitude=cLat)
proj_data = ccrs.PlateCarree() # Our data is lat-lon; thus its native projection is Plate Carree.
res = '50m'
constrainLon = 3.3

In [ ]:
def make_regional_map(i, z):
    
    fig = plt.figure(figsize=(18, 12))
    ax = plt.subplot(1,1,1,projection=proj_map)
    ax.set_extent ([lonW + constrainLon,lonE - constrainLon,latS,latN])
    ax.add_feature(cfeature.COASTLINE.with_scale(res))
    ax.add_feature(cfeature.STATES.with_scale(res))

    # Add the title
    valTime = pd.to_datetime(SLP.time[i].values).strftime("%m/%d/%Y at %H UTC")
    tl1 = str("ERA-5 SLP and " + str(pLevel) + "hPa Z, " + valTime)
    plt.title(tl1,fontsize=16)

    # Height (Z) contour fills
    
    CF = ax.contourf(lons,lats,z,levels=zLevels,cmap=plt.get_cmap('viridis'), extend='both', transform=proj_data)
    cbar = fig.colorbar(CF,shrink=0.5)
    cbar.set_label(r'Heights (dam)', size='medium')
    
    # SLP contour lines
    CL = ax.contour(lons,lats,SLP.isel(time=i),slpLevels,linewidths=1.25,colors='chocolate', transform=proj_data)
    ax.clabel(CL, inline_spacing=0.2, fontsize=8, fmt='%.0f');

   

Create a `for` loop and loop through the times. In this loop, we will also pass in the geopotential grid, and convert its units from geopotential to decameters.

<div class="alert alert-warning">In general, we ought to have been able to perform this conversion on the original, multi-hour data array. However, it appears that once again this is not possible when reading from a THREDDS data server such as RDA's; we need to operate on only one single time.</div>

<div class="alert alert-info"><b>Note: </b>In this example, to save time we have set the hour increment to <b>12</b> in the cell below ... so we will have two graphics per loop. When you are ready to run this on your own case, change the increment to <b>1</b> so you get 24 hours worth of maps!</div> 

In [ ]:
inc = 12 # change to 1 when you are ready
for time in range(0, 24, inc):
    z = mpcalc.geopotential_to_height(Z.isel(time=time)).metpy.convert_units('dam')
    make_global_map(time, z)
    make_regional_map(time,z) # This will take some time, be patient!

    print(time)

---
### Things to try
1. Once you have run through this notebook, make a copy of it and choose another weather event. **The ERA-5 now extends all the way back to 1950!!**
1. Next, create some different visualizations, using the many variables in the ERA-5. For example:
- 850 hPa heights and temperature
- 300 hPa heights and isotachs
- Snow depth
- Accumulated precipitation 
- Sea surface temperature
---

#### "The sky's the limit!" (or, "There is an endless sea of possibilities!")
Ultimately, you and your team members will create 4 different 24-hour time loops for the weather event you have chosen.

---
### What's next?
In the next notebook, we will create a similar set of graphics, but save them to disk in a format amenable for loading on our Science on a Sphere!